In [54]:
import netgen.gui
from ngsolve import *
import netgen.geom2d as geom2d

geo = geom2d.SplineGeometry()
geo.AddRectangle((-1,-1), (1,1), bcs=["bottom", "right", "top", "left"])
mesh = Mesh(geo.GenerateMesh(maxh=0.05))
mesh.GetBoundaries()

('bottom', 'right', 'top', 'left')

In [55]:
fes = H1(mesh, order=2, dirichlet="left|right|top|bottom")

In [56]:
g = 2*exp(-1.5*(x**2 + y**2))

In [57]:
gfu = GridFunction(fes)
gfu.Set(g, definedon=mesh.Boundaries("left|right|top|bottom"))
Draw(gfu)

In [58]:
u, v = fes.TnT()
a = BilinearForm(fes)
a += grad(u)*grad(v)*dx
f = LinearForm(fes)
f += (-(18*x*x-6)*exp(-1.5*(x*x + y*y))-(18*y*y-6)*exp(-1.5*(x*x + y*y)))*v*dx
c = Preconditioner(a,"multigrid")

In [59]:
space_flux = HDiv(mesh, order=2)
gf_flux = GridFunction(space_flux, "flux")

In [60]:
def solveStep():
    fes.Update()
    gfu.Update()
    Draw(gfu)
    a.Assemble()
    f.Assemble()
    solvers.BVP(bf=a, lf=f, gf=gfu, pre=c)
    gfu.Update()
    Redraw(blocking=True)

In [61]:
def estimateError():
    space_flux.Update()
    gf_flux.Update()
    flux = grad(gfu)
    gf_flux.Set(flux) 
    
    err = (flux-gf_flux)*(flux-gf_flux)
    Draw(err, mesh, 'error_representation')
    eta2 = Integrate(err, mesh, VOL, element_wise=True)
    
    maxerr = max(eta2)
    for el in mesh.Elements():
        mesh.SetRefinementFlag(el, eta2[el.nr] > 0.25*maxerr)

In [62]:
solveStep()

iteration 0 error = 5.872388416977667
iteration 1 error = 0.09954130907157585
iteration 2 error = 0.0012386040691894527
iteration 3 error = 3.166745218856071e-05
iteration 4 error = 7.693258931855154e-07
iteration 5 error = 1.116749630228875e-08


In [63]:
estimateError()

In [64]:
mesh.Refine()

In [65]:
solveStep()

iteration 0 error = 3.2792302842649628
iteration 1 error = 0.007748727760904808
iteration 2 error = 0.0004669245820593913
iteration 3 error = 4.8789480137635376e-05
iteration 4 error = 5.628622884735156e-06
iteration 5 error = 7.152977255435855e-07
iteration 6 error = 8.681503992079707e-08
iteration 7 error = 1.0289554763295419e-08


In [66]:
Draw(gfu)